In [ ]:
import numpy as np
import pandas as pd

In [ ]:
from google.colab import files

uploaded = files.upload()

for fn in uploaded.keys():
  print('User uploaded file "{name}" with length {length} bytes'.format(
      name=fn, length=len(uploaded[fn])))

In [ ]:
import io
df = pd.read_csv(io.StringIO(uploaded['fake_job_postings.csv'].decode('utf-8')))
df.head()

In [ ]:
import numpy as np 
from scipy.stats import pearsonr
from sklearn.preprocessing import LabelEncoder
from sklearn.decomposition import PCA
from sklearn.model_selection import train_test_split
from sklearn.metrics import accuracy_score
from sklearn.metrics import classification_report
#from sklearn.metrics import accuracy_score
import seaborn as sns;sns.set(style="ticks", color_codes=True)
import matplotlib.pyplot as plt
import plotly.graph_objs as go
from plotly.subplots import make_subplots
import seaborn as sns
import cufflinks as cf
import plotly.express as px
%matplotlib inline
import warnings
warnings.filterwarnings('ignore')
from plotly.offline import download_plotlyjs, init_notebook_mode, plot, iplot
init_notebook_mode(connected = True)
cf.go_offline() 

#from sklearn.model_selection import train_test_split
from sklearn import metrics
from sklearn.metrics import mean_squared_error

**Transforming into numerical**

In [ ]:
from sklearn.preprocessing import LabelEncoder
lbencder=LabelEncoder()
def lencoder_feature(x_labels):
    lbencder=LabelEncoder()
    x_labels=lbencder.fit_transform(x_labels)
    return x_labels
df=df.apply(lencoder_feature)
df.head()

In [ ]:
df.info()

In [ ]:
feature=df.drop(columns=['fraudulent'])
label=df['fraudulent']

In [ ]:
from scipy.stats import pearsonr

corre=pd.DataFrame()

for i in feature.columns:
    corre[i]= pearsonr(label, feature[i])
    
    
corre

In [ ]:
corre1=corre.T
corre1
corre1

In [ ]:
corre1=corre.T
corre1
coore2= corre1.iloc[:,0].sort_values(ascending=False)
coore2
coore2= corre1.iloc[:,0].sort_values(ascending=False)
coore2

Features Selection(Reducing Dimension)

In [ ]:
feature=df.drop(columns=['fraudulent'])
label=df['fraudulent']

from sklearn.decomposition import PCA
from sklearn.metrics import accuracy_score
Transf_pca = PCA(n_components= 13)
datanew = Transf_pca.fit_transform(feature)
print(datanew)
datanew.shape

In [ ]:
datanew

In [ ]:
label=pd.DataFrame(label)
label.shape
newbase=np.concatenate((datanew,label),axis=1)
print(newbase)
newbase.shape
newbase=pd.DataFrame(newbase)
print(newbase.columns)

In [ ]:
newbase # new dataset with only 10 independent variables after reduction

separating fake and real jobs and do a prediction using OneClass SVM for fake jobs

In [ ]:
dataset_selected1=newbase.loc[newbase[13].isin([1])]
dataset_selected0=newbase.loc[newbase[13].isin([0])]


#on va diviser dataset_selected1 en 2 partie data1 et label1
label1=dataset_selected1[13]
data1=dataset_selected1.drop([13],axis=1)

#on va diviser dataset_selected0 en 2 partie data0 et label0
label0=dataset_selected0[13]
#remplacer 0 par -1
label0=label0-1
data0=dataset_selected0.drop([13],axis=1)

In [ ]:
from sklearn.model_selection import train_test_split
x_train1,x_test1,y_train1,y_test1=train_test_split(data1,label1,test_size=0.33,random_state=0)
from sklearn import svm
model=svm.OneClassSVM(kernel='rbf',nu=1,gamma=0.00001)
import time
debut=time.time()
model.fit(x_train1)
fin=time.time()-debut

In [ ]:
import numpy as np
data_tesst=np.concatenate((x_test1,data0),axis=0)
label_tesst=np.concatenate((y_test1,label0),axis=0)
pred=model.predict(data_tesst)

In [ ]:
from sklearn.metrics import accuracy_score
ACC=accuracy_score(label_tesst,pred)*100
print('the accurency score is :')
print(ACC)

In [ ]:
from sklearn.metrics import classification_report
print(classification_report(label_tesst,pred))

predict fake jobs after using PCA to reduce dimension

In [ ]:
print(newbase)
label=newbase[13]
data=newbase.drop([13],axis=1)

In [ ]:
label.value_counts()

Using RandomOversampling to deal with imabalanced data

In [ ]:
from imblearn.over_sampling import RandomOverSampler
import imblearn
print(imblearn.__version__)

# define oversampling strategy
oversample = RandomOverSampler(sampling_strategy='minority')

# define oversampling strategy
oversample = RandomOverSampler(sampling_strategy=1.0)

# fit and apply the transform
X_over, y_over = oversample.fit_resample(feature, label)
#compter combien de 1 et de 0 dans dataset
label=y_over
data=X_over
label =pd.DataFrame(label)
label.value_counts()

In [ ]:
data.info()

In [ ]:
#data = data.drop(['salary_range', 'department' , 'required_education' , 'benefits'], axis=1)

In [ ]:
data

In [ ]:
from sklearn.model_selection import train_test_split
x_train,x_test,y_train,y_test = train_test_split(data,label,test_size = 0.3,random_state = 0)

In [ ]:
x_test

**Feature Scaling**

In [ ]:
from sklearn.preprocessing import StandardScaler
sc_X = StandardScaler()
x_train = sc_X.fit_transform(x_train)
x_test = sc_X.transform(x_test)

In [ ]:
x_test

Applying Decision Tree Classifier to predict fakeor real posting jobs

In [ ]:
from sklearn.tree import DecisionTreeClassifier
dtree = DecisionTreeClassifier()
import time
debut=time.time()
dtree.fit(x_train,y_train)
fin=time.time()-debut
prediction = dtree.predict(x_test)

In [ ]:
from sklearn.metrics import accuracy_score
ACC=accuracy_score(y_test,prediction)*100
print('With decision tree accuracy is: ',ACC) # accuracy

In [ ]:
from sklearn.metrics import confusion_matrix
cm = confusion_matrix(y_test,prediction)
print(cm)

# **AdaBoost Classifier**

In [ ]:
from sklearn.ensemble import AdaBoostClassifier
abc = AdaBoostClassifier(n_estimators=1600,
                         random_state=0)
model = abc.fit(x_train, y_train)

y_pred = model.predict(x_test)

Accuracy (AB)

In [ ]:
from sklearn.metrics import accuracy_score
ACC=accuracy_score(y_test,y_pred)*100
print('With AdaBoost accuracy is: ',ACC) # accuracy

Kappa Value

In [ ]:
from sklearn.metrics import cohen_kappa_score

cohen_kappa_score(y_test,y_pred)

**Confusion Matrix**

In [ ]:
from sklearn.metrics import confusion_matrix
cm = confusion_matrix(y_test,y_pred)
print(cm)

**Performance/Calssification_Report**

In [ ]:
from sklearn.metrics import classification_report
print("Classification Report: \n", classification_report(y_test,y_pred))

**Roc Curve**

In [ ]:
from sklearn import metrics
fpr, tpr, thresholds = metrics.roc_curve(y_test,y_pred)
plt.plot(fpr, tpr)
plt.xlim([0.0, 1.0])
plt.ylim([0.0, 1.0])
plt.title('Receiver Operating Characteristic of AB')
plt.xlabel('False Positive Rate')
plt.ylabel('True Positive Rate')
plt.grid(True)
print('\n\n\n FPR, TPR, and Thresholds')
print("False Positive Rate:", fpr) # value between 0 and 1
print("True Positive Rate:", tpr)  # value between 0 and 1, The curve is based on fpr and tpr values only.
print("Thresholds: ", thresholds) 

# XGBoost classifier

In [ ]:
import xgboost as xgb
xg_reg = xgb.XGBRegressor(max_depth = 5, n_estimators = 110)
                
model = xg_reg.fit(x_train,y_train)

preds = model.predict(x_test)

**Accuracy**

In [ ]:
from sklearn.metrics import accuracy_score
ACC=accuracy_score(y_test,preds.round())*100
print('With XgBoost accuracy is: ',ACC)

In [ ]:
from sklearn.metrics import cohen_kappa_score

cohen_kappa_score(y_test,preds.round())

**Confusion Matrix**

In [ ]:
from sklearn.metrics import confusion_matrix
cm = confusion_matrix(y_test,preds.round())
print(cm)

**Performance/Calssification_Report**

In [ ]:
from sklearn.metrics import classification_report
print("Classification Report: \n", classification_report(y_test,preds.round()))

**ROC Curve**

In [ ]:
from sklearn import metrics
fpr, tpr, thresholds = metrics.roc_curve(y_test,preds.round())
plt.plot(fpr, tpr)
plt.xlim([0.0, 1.0])
plt.ylim([0.0, 1.0])
plt.title('Receiver Operating Characteristic of XGB')
plt.xlabel('False Positive Rate')
plt.ylabel('True Positive Rate')
plt.grid(True)
print('\n\n\n FPR, TPR, and Thresholds')
print("False Positive Rate:", fpr) # value between 0 and 1
print("True Positive Rate:", tpr)  # value between 0 and 1, The curve is based on fpr and tpr values only.
print("Thresholds: ", thresholds) 

## Bagging

In [ ]:
from sklearn.ensemble import BaggingClassifier
from sklearn.svm import SVC
model = BaggingClassifier(base_estimator = SVC(),
                          n_estimators = 200,
                          random_state = 8)
model.fit(x_train, y_train)
bag_predict = model.predict(x_test)

In [ ]:
ACC=accuracy_score(y_test,bag_predict)*100
print('With Bagging accuracy is: ',ACC)

kappa values

In [ ]:
from sklearn.metrics import cohen_kappa_score

cohen_kappa_score(y_test,bag_predict)

In [ ]:
from sklearn.metrics import confusion_matrix
cm = confusion_matrix(y_test,bag_predict)
print(cm)

In [ ]:
from sklearn.metrics import classification_report
print("Classification Report: \n", classification_report(y_test, bag_predict))

## Voting

In [ ]:
from sklearn.ensemble import VotingClassifier
from sklearn.linear_model import LogisticRegression
from sklearn.neighbors import KNeighborsClassifier
knn_clf=KNeighborsClassifier()
lr=LogisticRegression()
#instantiating three classifiers
logReg= LogisticRegression()
dTree= DecisionTreeClassifier()
svm= SVC()
voting_clf = VotingClassifier(estimators=[('SVC', svm), ('DecisionTree',dTree), ('LogReg', logReg), ('KNN', knn_clf)], voting='hard')
#fit and predict using training and testing dataset respectively
voting_clf.fit(x_train, y_train)
vt_predict = voting_clf.predict(x_test)


In [ ]:
ACC=accuracy_score(y_test,vt_predict)*100
print('With Voting accuracy is: ',ACC)

In [ ]:
from sklearn.metrics import cohen_kappa_score

cohen_kappa_score(y_test,vt_predict)

In [ ]:
from sklearn.metrics import confusion_matrix
cm = confusion_matrix(y_test,vt_predict)
print(cm)

In [ ]:
from sklearn.metrics import classification_report
print("Classification Report: \n", classification_report(y_test,vt_predict))

In [ ]:
from sklearn import metrics
fpr, tpr, thresholds = metrics.roc_curve(y_test,vt_predict)
plt.plot(fpr, tpr)
plt.xlim([0.0, 1.0])
plt.ylim([0.0, 1.0])
plt.title('Receiver Operating Characteristic of Voting')
plt.xlabel('False Positive Rate')
plt.ylabel('True Positive Rate')
plt.grid(True)
print('\n\n\n FPR, TPR, and Thresholds')
print("False Positive Rate:", fpr) # value between 0 and 1
print("True Positive Rate:", tpr)  # value between 0 and 1, The curve is based on fpr and tpr values only.
print("Thresholds: ", thresholds)

## Random Forest

In [ ]:
from sklearn.ensemble import RandomForestClassifier

rf=RandomForestClassifier(n_estimators=10, criterion = 'entropy', max_depth=10, random_state=8)

rf.fit(x_train,y_train)

rf_pred=rf.predict(x_test)

In [ ]:
ACC=accuracy_score(y_test,rf_pred)*100
print('With Random Forest accuracy is: ',ACC)

In [ ]:
from sklearn.metrics import cohen_kappa_score

cohen_kappa_score(y_test,rf_pred)

In [ ]:
from sklearn.metrics import confusion_matrix
cm = confusion_matrix(y_test,rf_pred)
print(cm)

In [ ]:

from sklearn.metrics import classification_report
print("Classification Report: \n", classification_report(y_test,rf_pred))

In [ ]:
from sklearn import metrics
fpr, tpr, thresholds = metrics.roc_curve(y_test,rf_pred)
plt.plot(fpr, tpr)
plt.xlim([0.0, 1.0])
plt.ylim([0.0, 1.0])
plt.title('Receiver Operating Characteristic of RF')
plt.xlabel('False Positive Rate')
plt.ylabel('True Positive Rate')
plt.grid(True)
print('\n\n\n FPR, TPR, and Thresholds')
print("False Positive Rate:", fpr) # value between 0 and 1
print("True Positive Rate:", tpr)  # value between 0 and 1, The curve is based on fpr and tpr values only.
print("Thresholds: ", thresholds) 